### Single Pass Spectrogram Inversion

Reconstruct an audio signal from a magnitude spectrum with but a single ifft.<br>

Cite and more info: <br>
    Beauregard, G., Harish, M. and Wyse, L. (2015), Single Pass Spectrogram Inversion, <br>
    in Proceedings of the IEEE International Conference on Digital Signal Processing. Singapore, 2015.<br>
    [Phase reconstruction homepage.](http://anclab.org/software/phaserecon/)
    
### This is the work of mclonce. I only added something to automatically scan and process all files in a given folder
https://github.com/lonce/SPSI_Python

In [8]:
import numpy as np
import librosa
import math
import scipy

print('You are using librosa version ' + librosa.__version__)

You are using librosa version 0.6.3


In [9]:
def spsi(msgram, fftsize, hop_length) :
    """
    Takes a 2D spectrogram ([freqs,frames]), the fft legnth (= widnow length) and the hope size (both in units of samples).
    Returns an audio signal.
    """
    
    numBins, numFrames  = msgram.shape
    y_out=np.zeros(numFrames*hop_length+fftsize-hop_length)
        
    m_phase=np.zeros(numBins);      
    m_win=scipy.signal.hanning(fftsize, sym=True)  # assumption here that hann was used to create the frames of the spectrogram
    
    #processes one frame of audio at a time
    for i in range(numFrames) :
            m_mag=msgram[:, i] 
            for j in range(1,numBins-1) : 
                if(m_mag[j]>m_mag[j-1] and m_mag[j]>m_mag[j+1]) : #if j is a peak
                    alpha=m_mag[j-1];
                    beta=m_mag[j];
                    gamma=m_mag[j+1];
                    denom=alpha-2*beta+gamma;
                    
                    if(denom!=0) :
                        p=0.5*(alpha-gamma)/denom;
                    else :
                        p=0;
                        
                    #phaseRate=2*math.pi*(j-1+p)/fftsize;    #adjusted phase rate
                    phaseRate=2*math.pi*(j+p)/fftsize;    #adjusted phase rate
                    m_phase[j]= m_phase[j] + hop_length*phaseRate; #phase accumulator for this peak bin
                    peakPhase=m_phase[j];
                    
                    # If actual peak is to the right of the bin freq
                    if (p>0) :
                        # First bin to right has pi shift
                        bin=j+1;
                        m_phase[bin]=peakPhase+math.pi;
                        
                        # Bins to left have shift of pi
                        bin=j-1;
                        while((bin>1) and (m_mag[bin]<m_mag[bin+1])) : # until you reach the trough
                            m_phase[bin]=peakPhase+math.pi;
                            bin=bin-1;
                        
                        #Bins to the right (beyond the first) have 0 shift
                        bin=j+2;
                        while((bin<(numBins)) and (m_mag[bin]<m_mag[bin-1])) :
                            m_phase[bin]=peakPhase;
                            bin=bin+1;
                            
                    #if actual peak is to the left of the bin frequency
                    if(p<0) :
                        # First bin to left has pi shift
                        bin=j-1;
                        m_phase[bin]=peakPhase+math.pi;

                        # and bins to the right of me - here I am stuck in the middle with you
                        bin=j+1;
                        while((bin<(numBins)) and (m_mag[bin]<m_mag[bin-1])) :
                            m_phase[bin]=peakPhase+math.pi;
                            bin=bin+1;
                        
                        # and further to the left have zero shift
                        bin=j-2;
                        while((bin>1) and (m_mag[bin]<m_mag[bin+1])) : # until trough
                            m_phase[bin]=peakPhase;
                            bin=bin-1;
                            
                #end ops for peaks
            #end loop over fft bins with

            magphase=m_mag*np.exp(1j*m_phase)  #reconstruct with new phase (elementwise mult)
            magphase[0]=0; magphase[numBins-1] = 0 #remove dc and nyquist
            m_recon=np.concatenate([magphase,np.flip(np.conjugate(magphase[1:numBins-1]), 0)]) 
            
            #overlap and add
            m_recon=np.real(np.fft.ifft(m_recon))*m_win
            y_out[i*hop_length:i*hop_length+fftsize]+=m_recon
            
    return y_out

In [15]:
# Test
import matplotlib.pyplot as plt
%matplotlib inline
import librosa.display
import IPython.display
import os
import re

fftsize=1024
hop_length=512
##UPDATE FOLDERS HERE TO YOUR FOLDER WITH WAV-MUSIC:
##UPDATE FOLDERS HERE TO YOUR FOLDER WITH WAV-MUSIC:
##UPDATE FOLDERS HERE TO YOUR FOLDER WITH WAV-MUSIC:
dest = '/Volumes/LaCie/power_metai/'

wav_list = []
for root, dirs, files in os.walk(dest +'/wav/only_three_wav/'):
    for filename in files:
        wav_list.append(re.split('wav',filename)[0])
try:
    wav_list.remove('.DS_Store')
except:
    print('No DS_Store to remove! All ok!')
i = 1
for name in wav_list:
    try:
        music = dest + 'wav/only_three_wav/'+name+ 'wav'
        print(music)
        print('Currently {} of {}.'.format(i, len(wav_list)))
        #y, sr = librosa.load('sounds/BeingRural_short.wav')
        y, sr = librosa.load(music, offset=5, duration=25)

        D = librosa.stft(y, fftsize, hop_length=hop_length)
        magD=np.abs(D)
        logMagD= librosa.amplitude_to_db(magD,ref=np.max)

        ax = librosa.display.specshow(logMagD)
        #plt.colorbar(format='%+2.0f dB')

        y_out = spsi(magD, fftsize=fftsize, hop_length=hop_length)
        print('Success! Saving picture as:',dest + 'specto/'+name + '.png')
        plt.axis('off') # this rows the rectangular frame 
        ax.get_xaxis().set_visible(False) # this removes the ticks and numbers for x axis
        ax.get_yaxis().set_visible(False) # this removes the ticks and numbers for y axis
        plt.savefig(dest + 'specto/only_three_specto/'+name + 'png', dpi=300,bbox_inches="tight", pad_inches=0)
        plt.clf()
        i += 1
    except: 
        print('There is an error with {}. I skip it!'.format(name))

No DS_Store to remove! All ok!
/Volumes/LaCie/power_metai/wav/only_three_wav/4th Dimension - Kingdom of Thyne Illusions.wav
Currently 1 of 3.


/Users/vtimmel/anaconda3/envs/tf_2_alpha/lib/python3.7/site-packages/ipykernel_launcher.py:11: DeprecationWarning: `hanning` is deprecated, use `scipy.signal.windows.hann` instead!
  # This is added back by InteractiveShellApp.init_path()


Success! Saving picture as: /Volumes/LaCie/power_metai/specto/4th Dimension - Kingdom of Thyne Illusions..png
/Volumes/LaCie/power_metai/wav/only_three_wav/Orden Ogan - To the End.wav
Currently 2 of 3.
Success! Saving picture as: /Volumes/LaCie/power_metai/specto/Orden Ogan - To the End..png
/Volumes/LaCie/power_metai/wav/only_three_wav/Twilightning - At The Forge.wav
Currently 3 of 3.
Success! Saving picture as: /Volumes/LaCie/power_metai/specto/Twilightning - At The Forge..png


<Figure size 432x288 with 0 Axes>

In [17]:
# Original
IPython.display.Audio(data=y, rate=sr)

In [20]:
# Single pass reconstruction from mag spectrogram
IPython.display.Audio(data=y_out, rate=sr)

Note: Try this as an initial phase estimate for Griffin & Lim reconstruction to save time and electricity!

In [21]:
p = np.angle(librosa.stft(y_out, fftsize, hop_length, center=False))
for i in range(50):
    S = magD * np.exp(1j*p)
    x = librosa.istft(S, hop_length, center=True) # Griffin Lim, assumes hann window; librosa only does one iteration?
    p = np.angle(librosa.stft(x, fftsize, hop_length, center=True))

IPython.display.Audio(data=x.T, rate=sr)